In [0]:
import os
import json
from tqdm import tqdm
# import torch, torchvision
# import detectron2

# from detectron2.utils.logger import setup_logger
# setup_logger()


# import numpy as np
# import cv2
# import random
# from google.colab.patches import cv2_imshow


# from detectron2 import model_zoo
# from detectron2.engine import DefaultPredictor
# from detectron2.config import get_cfg
# from detectron2.utils.visualizer import Visualizer
# from detectron2.data import MetadataCatalog

# from detectron2.checkpoint import DetectionCheckpointer


In [0]:
# install dependencies: (use cu101 because colab has CUDA 10.1)
!pip install -U torch==1.5 torchvision==0.6 -f https://download.pytorch.org/whl/cu101/torch_stable.html 
!pip install cython pyyaml==5.1
# !pip install -U 'git+https://github.com/cocodataset/cocoapi.git#subdirectory=PythonAPI'
# import torch, torchvision
# print(torch.__version__, torch.cuda.is_available())
!gcc --version
# opencv is pre-installed on colab

Looking in links: https://download.pytorch.org/whl/cu101/torch_stable.html
Requirement already up-to-date: torch==1.5 in /usr/local/lib/python3.6/dist-packages (1.5.0+cu101)
Requirement already up-to-date: torchvision==0.6 in /usr/local/lib/python3.6/dist-packages (0.6.0+cu101)
     |████████████████████████████████| 276kB 8.8MB/s 
  Created wheel for pyyaml: filename=PyYAML-5.1-cp36-cp36m-linux_x86_64.whl size=44074 sha256=a0443268d1de43c948d718cd6fe9606d21e1fe1cc20e6ebc303179a840f2875d
  Stored in directory: /root/.cache/pip/wheels/ad/56/bc/1522f864feb2a358ea6f1a92b4798d69ac783a28e80567a18b
Successfully built pyyaml
  Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
gcc (Ubuntu 7.5.0-3ubuntu1~18.04) 7.5.0
Copyright (C) 2017 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



In [0]:
# install detectron2:
!pip3 install detectron2==0.1.2 -f https://dl.fbaipublicfiles.com/detectron2/wheels/cu101/index.html

Looking in links: https://dl.fbaipublicfiles.com/detectron2/wheels/cu101/index.html
     |████████████████████████████████| 6.2MB 598kB/s 
  Created wheel for fvcore: filename=fvcore-0.1.1.post200513-cp36-none-any.whl size=40893 sha256=b97e1395a3830f008dca02d19dd18e32f321bae66cb7ff460fdc5a5b4d1801f6
  Stored in directory: /root/.cache/pip/wheels/a2/f6/77/551770c4b8cd75e9335cd0acf59c08d60a8684048b19da6702
Successfully built fvcore


In [0]:
# You may need to restart your runtime prior to this, to let your installation take effect
# Some basic setup:
# Setup detectron2 logger
import detectron2
from detectron2.utils.logger import setup_logger
setup_logger()
import torch, torchvision
# import some common libraries
import numpy as np
import cv2
import random
from google.colab.patches import cv2_imshow

# import some common detectron2 utilities
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog

from detectron2.checkpoint import DetectionCheckpointer
from detectron2.data.datasets import register_coco_instances


from pycocotools.coco import COCO
from detectron2.engine import DefaultTrainer
from detectron2.config import get_cfg
from detectron2.structures import Boxes, BoxMode, pairwise_iou
import pycocotools.mask as mask_util



In [0]:
os.chdir("/content/drive/My Drive/DrawnAI/")

In [0]:
register_coco_instances("my_dataset_train", {}, "/content/drive/My Drive/DrawnAI/data/train/coco_train_v1.json", "/content/drive/My Drive/DrawnAI/data/train/train_images/")
register_coco_instances("my_dataset_val", {}, "/content/drive/My Drive/DrawnAI/data/train/coco_val_v1.json", "/content/drive/My Drive/DrawnAI/data/train/train_images/")

In [0]:
json_file = "/content/drive/My Drive/DrawnAI/data/train/coco_train_v1.json"
coco_api = COCO(json_file)
dataset_name = "my_dataset_train"
id_map = None
if dataset_name is not None:
    meta = MetadataCatalog.get(dataset_name)
    cat_ids = sorted(coco_api.getCatIds())
    cats = coco_api.loadCats(cat_ids)
    # The categories in a custom json file may not be sorted.
    thing_classes = [c["name"] for c in sorted(cats, key=lambda x: x["id"])]
    meta.thing_classes = thing_classes

    # In COCO, certain category ids are artificially removed,
    # and by convention they are always ignored.
    # We deal with COCO's id issue and translate
    # the category ids to contiguous ids in [0, 80).

    # It works by looking at the "categories" field in the json, therefore
    # if users' own json also have incontiguous ids, we'll
    # apply this mapping as well but print a warning.
    if not (min(cat_ids) == 1 and max(cat_ids) == len(cat_ids)):
        if "coco" not in dataset_name:
          print("We will apply mapping to you")
    id_map = {v: i for i, v in enumerate(cat_ids)}
    meta.thing_dataset_id_to_contiguous_id = id_map

loading annotations into memory...
Done (t=1.49s)
creating index...
index created!
We will apply mapping to you


In [0]:
dataset_name = "my_dataset_val"
metadata = MetadataCatalog.get(dataset_name)

In [0]:
metadata

Metadata(evaluator_type='coco', image_root='/content/drive/My Drive/DrawnAI/data/train/train_images/', json_file='/content/drive/My Drive/DrawnAI/data/train/coco_val_v1.json', name='my_dataset_val', thing_classes=['paragraph', 'dropdown', 'checkbox', 'radiobutton', 'rating', 'toggle', 'textarea', 'datepicker', 'stepperinput', 'slider', 'video', 'label', 'table', 'list', 'header', 'button', 'image', 'linebreak', 'container', 'link', 'textinput'], thing_dataset_id_to_contiguous_id={0: 0, 1: 1, 2: 2, 3: 3, 4: 4, 5: 5, 6: 6, 7: 7, 8: 8, 9: 9, 10: 10, 11: 11, 12: 12, 13: 13, 14: 14, 15: 15, 16: 16, 17: 17, 18: 18, 19: 19, 20: 20})

In [0]:
categories = [{"id": id, "name": name} for id, name in enumerate(metadata.thing_classes)]

In [0]:
categories

[{'id': 0, 'name': 'paragraph'},
 {'id': 1, 'name': 'dropdown'},
 {'id': 2, 'name': 'checkbox'},
 {'id': 3, 'name': 'radiobutton'},
 {'id': 4, 'name': 'rating'},
 {'id': 5, 'name': 'toggle'},
 {'id': 6, 'name': 'textarea'},
 {'id': 7, 'name': 'datepicker'},
 {'id': 8, 'name': 'stepperinput'},
 {'id': 9, 'name': 'slider'},
 {'id': 10, 'name': 'video'},
 {'id': 11, 'name': 'label'},
 {'id': 12, 'name': 'table'},
 {'id': 13, 'name': 'list'},
 {'id': 14, 'name': 'header'},
 {'id': 15, 'name': 'button'},
 {'id': 16, 'name': 'image'},
 {'id': 17, 'name': 'linebreak'},
 {'id': 18, 'name': 'container'},
 {'id': 19, 'name': 'link'},
 {'id': 20, 'name': 'textinput'}]

In [0]:
dataset_name = "my_dataset_train"
meta = MetadataCatalog.get(dataset_name)
if hasattr(meta, "thing_dataset_id_to_contiguous_id"):
            print("Hello")
            reverse_id_mapping = {
                v: k for k, v in meta.thing_dataset_id_to_contiguous_id.items()
            }

Hello


In [0]:
type(reverse_id_mapping_val)

NameError: ignored

In [0]:
reverse_id_mapping

{0: 0,
 1: 1,
 2: 2,
 3: 3,
 4: 4,
 5: 5,
 6: 6,
 7: 7,
 8: 8,
 9: 9,
 10: 10,
 11: 11,
 12: 12,
 13: 13,
 14: 14,
 15: 15,
 16: 16,
 17: 17,
 18: 18,
 19: 19,
 20: 20}

In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/")
with open("reverse_id_mapping.json", "w") as write_file:
    json.dump(reverse_id_mapping, write_file)

In [0]:
if(reverse_id_mapping==reverse_id_mapping_val):
  print("yessss")
else:
  print("Sad")  

yessss


In [0]:
for k,v in reverse_id_mapping.items():
  print(v," ",reverse_id_mapping_val[k])
  if(v!=reverse_id_mapping_val[k]):
    print("oh sad")


1010   1010
1013   1013
1022   1022
1026   1026
1032   1032
1040   1040
1056   1056
1058   1058
1060   1060
1061   1061
1068   1068
1069   1069
1070   1070
1078   1078
1085   1085
1108   1108
1116   1116
1151   1151
1154   1154
1163   1163
1180   1180
1210   1210
1220   1220
1307   1307
1310   1310
1311   1311
1323   1323
1352   1352
1468   1468
1505   1505
1520   1520
1554   1554
1556   1556
1565   1565
1566   1566
1588   1588
1788   1788
1879   1879
1893   1893
1967   1967
2022   2022
2053   2053
2099   2099
2103   2103
2131   2131
2388   2388
2498   2498
2504   2504
2512   2512
2521   2521
2530   2530
2578   2578
2580   2580
2618   2618
2620   2620
2634   2634
2711   2711
2738   2738
2750   2750
2939   2939
3080   3080


In [0]:
import json
with open('/content/drive/My Drive/DrawnAI/data/train/coco_val_v1.json') as json_file:
    valjson = json.load(json_file)

with open('/content/drive/My Drive/DrawnAI/data/train/coco_train_v1.json') as json_file:
    trainjson = json.load(json_file)

In [0]:
print("Train images ", len(trainjson['images']))
print("Train categories ", len(trainjson['categories']))

print("Val images ", len(valjson['images']))
print("Val categories ", len(valjson['categories']))

Train images  1891
Train categories  21
Val images  472
Val categories  21


In [0]:
for i in trainjson['annotations']:
  if(i['category_id']>20):
    print(i)

for i in valjson['annotations']:
  if(i['category_id']==20):
    print(i)  

{'image_id': '00af306dc45f95aa', 'bbox': [625, 269, 174, 52], 'category_id': 20, 'id': 53267, 'iscrowd': 0, 'area': 9048}
{'image_id': '00deaf97f509aeeb', 'bbox': [254, 439, 514, 84], 'category_id': 20, 'id': 53290, 'iscrowd': 0, 'area': 43176}
{'image_id': '00deaf97f509aeeb', 'bbox': [244, 564, 519, 95], 'category_id': 20, 'id': 53291, 'iscrowd': 0, 'area': 49305}
{'image_id': '00deaf97f509aeeb', 'bbox': [254, 689, 514, 90], 'category_id': 20, 'id': 53292, 'iscrowd': 0, 'area': 46260}
{'image_id': '00deaf97f509aeeb', 'bbox': [249, 805, 524, 100], 'category_id': 20, 'id': 53293, 'iscrowd': 0, 'area': 52400}
{'image_id': '010a25027df4e09b', 'bbox': [1455, 1029, 209, 39], 'category_id': 20, 'id': 53404, 'iscrowd': 0, 'area': 8151}
{'image_id': '010a25027df4e09b', 'bbox': [1455, 1075, 204, 50], 'category_id': 20, 'id': 53405, 'iscrowd': 0, 'area': 10200}
{'image_id': '010a25027df4e09b', 'bbox': [714, 510, 380, 105], 'category_id': 20, 'id': 53406, 'iscrowd': 0, 'area': 39900}
{'image_id':

In [0]:
valjson['annotations'][0]

{'area': 9353,
 'bbox': [380, 912, 199, 47],
 'category_id': 0,
 'id': 53212,
 'image_id': '005a1269ffaaac13',
 'iscrowd': 0}

In [0]:
reverse_id_mapping[21] = 21

In [0]:
test_images_path = AICROWD_TEST_IMAGES_PATH = "/content/drive/My Drive/DrawnAI/data/train/train_images/"
predictions_output_path= AICROWD_PREDICTIONS_OUTPUT_PATH = "/content/drive/My Drive/DrawnAI"
model_path = "/content/drive/My Drive/DrawnAI/output/retinanet_R_101_FPN_3x_7500epochs/model_final.pth"
cpu_device = torch.device("cpu")

In [0]:
#Solving extra category error in retinaNet
def instances_to_coco_json(instances, img_id):
    num_instance = len(instances)
    if num_instance == 0:
        return []

    boxes = instances.pred_boxes.tensor.numpy()
    boxes = BoxMode.convert(boxes, BoxMode.XYXY_ABS, BoxMode.XYWH_ABS)
    boxes = boxes.tolist()
    scores = instances.scores.tolist()
    classes = instances.pred_classes.tolist()

    has_mask = instances.has("pred_masks")
    if has_mask:
        rles = [
            mask_util.encode(np.array(mask[:, :, None], order="F", dtype="uint8"))[0]
            for mask in instances.pred_masks
        ]
        for rle in rles:
            rle["counts"] = rle["counts"].decode("utf-8")

    has_keypoints = instances.has("pred_keypoints")
    if has_keypoints:
        keypoints = instances.pred_keypoints

    results = []
    for k in range(num_instance):
        result = {
            "image_id": img_id,
            "category_id": classes[k],
            "bbox": boxes[k],
            "score": scores[k],
        }
        if has_mask:
            result["segmentation"] = rles[k]
    
        results.append(result)
    return results







cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-Detection/retinanet_R_101_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS = model_path
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.9   # set the testing threshold for this model
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 21
# cfg.MODEL.DEVICE = "cpu"
predictor = DefaultPredictor(cfg)

print("Done")

results = []
for i in tqdm(valjson['images']):
  img_path =test_images_path + i['file_name']
  im = cv2.imread(img_path)
  if(im is not None):
    outputs = predictor(im)
    instances = outputs["instances"].to(cpu_device)
    # print(outputs)
    fname = i['file_name'].split('.')[0]
    result = instances_to_coco_json(instances,fname)
    if(len(result)!=0):
      for p in result:
        matchId = p['category_id']
        p['category_id'] = reverse_id_mapping[matchId]
        results.append(p)       
    

Loading config /usr/local/lib/python3.6/dist-packages/detectron2/model_zoo/configs/COCO-Detection/../Base-RetinaNet.yaml with yaml.unsafe_load. Your machine may be at risk if the file contains malicious content.

  0%|          | 0/472 [00:00<?, ?it/s]

Done



  0%|          | 1/472 [00:00<01:45,  4.48it/s]

KeyError: ignored

In [0]:
len(results)

100

In [0]:
from detectron2.engine import DefaultTrainer
from detectron2.config import get_cfg
from detectron2.structures import Boxes, BoxMode, pairwise_iou
import pycocotools.mask as mask_util
from detectron2.structures import Boxes, BoxMode, pairwise_iou
import pycocotools.mask as mask_util

os.chdir("/content/drive/My Drive/FoodSegmentation/")

In [0]:
cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS ="/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/model_final.pth"
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.2   # set the testing threshold for this model
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 61
# cfg.MODEL.DEVICE = "cpu"
predictor = DefaultPredictor(cfg)


In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/data/val/test_images/images/")

In [0]:
os.listdir()[0]

'057781.jpg'

In [0]:
im = cv2.imread("/content/drive/My Drive/FoodSegmentation/data/val/test_images/images/057781.jpg")
outputs = predictor(im)

In [0]:
outputs

{'instances': Instances(num_instances=4, image_height=479, image_width=480, fields=[pred_boxes: Boxes(tensor([[ 52.0807, 181.5791, 307.6136, 444.5285],
         [112.4589, 156.3341, 381.2346, 355.4022],
         [ 78.2535, 114.8897, 366.7799, 360.2942],
         [139.1339, 212.0832, 354.2556, 439.3451]], device='cuda:0')), scores: tensor([0.6864, 0.3802, 0.3423, 0.2774], device='cuda:0'), pred_classes: tensor([ 1, 18,  1,  1], device='cuda:0'), pred_masks: tensor([[[False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          ...,
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False]],
 
         [[False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., Fals

In [0]:
from detectron2.structures import Boxes, BoxMode, pairwise_iou
import pycocotools.mask as mask_util

In [0]:
cpu_device = torch.device("cpu")
instances = outputs["instances"].to(cpu_device)

In [0]:
result = instances_to_coco_json(instances,"057781.jpg")

In [0]:
result

[{'bbox': [52.08070373535156,
   181.57911682128906,
   255.5329132080078,
   262.94940185546875],
  'category_id': 1,
  'image_id': '057781.jpg',
  'score': 0.6863908767700195,
  'segmentation': {'counts': '`Yc1<b>4L3M2N3M3M2N2N3M2N2N3M2N2N2N3M3M3WC\\No;o1dC_NP<\\2J6K4K5J6J6H8J6K4M4M2O1N2O2M2N2M3N2N2N2N2N3L3L4L4K6L3N2N3M2O1N3M2N3M3M2N3N2N1O2N1O1O2O0O101O0O101O000000001O0O10001O0000000000001O000000001O0000001O00000000001O000000000000000000000000001O000000000000000000O1000000000000O1000000O10000O10000O2O000O100O10000O1000000O10000O1000000O2O0O10000O2N10001N101N101O0O2O001N101O001O001N101O001O0O2O1O001N101O0O2N3L4L9ETg`2',
   'size': [479, 480]}},
 {'bbox': [112.45893859863281,
   156.33412170410156,
   268.77569580078125,
   199.0680389404297],
  'category_id': 18,
  'image_id': '057781.jpg',
  'score': 0.38022470474243164,
  'segmentation': {'counts': '_Sf1=^>8J3N3M2N2N2N2N3M2N2M3N2N1O1O2M2L4J6H9J5K5M3M3M3M3L4L4M3M3N2N2O1O1O1N2N2N2L5K4L4M3M3K5N2M3N2M3O1N2N200O1O1N2O1O1M3N2M3O10000O100O

In [0]:
outputs.keys()

dict_keys(['instances'])

In [0]:
outputs['instances']

Instances(num_instances=4, image_height=479, image_width=480, fields=[pred_boxes: Boxes(tensor([[ 52.0807, 181.5791, 307.6136, 444.5285],
        [112.4589, 156.3341, 381.2346, 355.4022],
        [ 78.2535, 114.8897, 366.7799, 360.2942],
        [139.1338, 212.0832, 354.2555, 439.3451]], device='cuda:0')), scores: tensor([0.6864, 0.3802, 0.3423, 0.2774], device='cuda:0'), pred_classes: tensor([ 1, 18,  1,  1], device='cuda:0'), pred_masks: tensor([[[False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         ...,
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False]],

        [[False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         

In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/data/train/images/")
countr = 0
for i in os.listdir():
  if(countr==20):
    break
  else:
    if('_' in i):
      img_path = "/content/drive/My Drive/FoodSegmentation/data/train/images/" + str(i[2:])
      # print(img_path)
    else:
      img_path ="/content/drive/My Drive/FoodSegmentation/data/train/images/" + str(i)
      # print(img_path)
  im = cv2.imread(img_path)
  outputs = predictor(im)
  print(outputs)
  countr+=1  


{'instances': Instances(num_instances=1, image_height=796, image_width=796, fields=[pred_boxes: Boxes(tensor([[189.2810, 137.3990, 693.7932, 677.5944]], device='cuda:0')), scores: tensor([0.2112], device='cuda:0'), pred_classes: tensor([2], device='cuda:0'), pred_masks: tensor([[[False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         ...,
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False],
         [False, False, False,  ..., False, False, False]]], device='cuda:0')])}
{'instances': Instances(num_instances=4, image_height=400, image_width=401, fields=[pred_boxes: Boxes(tensor([[ 89.6653,  68.8053, 333.2285, 342.8657],
        [ 39.6304,  17.6980, 377.0904, 392.2338],
        [ 64.6095, 120.5378, 262.8704, 383.1075],
        [ 77.4950, 210.9488, 349.1620, 400.0000]], device='cuda:0')), scores: tensor([0

In [0]:
def instances_to_coco_json(instances, img_id):
    """
    Dump an "Instances" object to a COCO-format json that's used for evaluation.

    Args:
        instances (Instances):
        img_id (int): the image id

    Returns:
        list[dict]: list of json annotations in COCO format.
    """
    num_instance = len(instances)
    if num_instance == 0:
        return []

    boxes = instances.pred_boxes.tensor.numpy()
    boxes = BoxMode.convert(boxes, BoxMode.XYXY_ABS, BoxMode.XYWH_ABS)
    boxes = boxes.tolist()
    scores = instances.scores.tolist()
    classes = instances.pred_classes.tolist()

    has_mask = instances.has("pred_masks")
    if has_mask:
        # use RLE to encode the masks, because they are too large and takes memory
        # since this evaluator stores outputs of the entire dataset
        rles = [
            mask_util.encode(np.array(mask[:, :, None], order="F", dtype="uint8"))[0]
            for mask in instances.pred_masks
        ]
        for rle in rles:
            # "counts" is an array encoded by mask_util as a byte-stream. Python3's
            # json writer which always produces strings cannot serialize a bytestream
            # unless you decode it. Thankfully, utf-8 works out (which is also what
            # the pycocotools/_mask.pyx does).
            rle["counts"] = rle["counts"].decode("utf-8")

    has_keypoints = instances.has("pred_keypoints")
    if has_keypoints:
        keypoints = instances.pred_keypoints

    results = []
    for k in range(num_instance):
        result = {
            "image_id": img_id,
            "category_id": classes[k],
            "bbox": boxes[k],
            "score": scores[k],
        }
        if has_mask:
            result["segmentation"] = rles[k]
        if has_keypoints:
            # In COCO annotations,
            # keypoints coordinates are pixel indices.
            # However our predictions are floating point coordinates.
            # Therefore we subtract 0.5 to be consistent with the annotation format.
            # This is the inverse of data loading logic in `datasets/coco.py`.
            keypoints[k][:, :2] -= 0.5
            result["keypoints"] = keypoints[k].flatten().tolist()
        results.append(result)
    return results


In [0]:
from detectron2.modeling import build_model
model = build_model(cfg)

In [0]:
model

GeneralizedRCNN(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
      (res2): Sequential(
        (0): BottleneckBlock

In [0]:
torch.cuda.current_device()

0

In [0]:
type(cfg)

detectron2.config.config.CfgNode

In [0]:
cfg.keys()

dict_keys(['VERSION', 'MODEL', 'INPUT', 'DATASETS', 'DATALOADER', 'SOLVER', 'TEST', 'OUTPUT_DIR', 'SEED', 'CUDNN_BENCHMARK', 'VIS_PERIOD', 'GLOBAL'])

In [0]:

from detectron2.evaluation import COCOEvaluator, inference_on_dataset
from detectron2.data import build_detection_test_loader
evaluator = COCOEvaluator("my_dataset_val", cfg, False, output_dir="./output/evaluationchecker/")
val_loader = build_detection_test_loader(cfg, "my_dataset_val")
valResults = inference_on_dataset(trainer.model, val_loader, evaluator)

WARNING [05/11 19:10:16 d2.data.datasets.coco]: 
Category ids in annotations are not in [1, #categories]! We'll apply a mapping for you.

[05/11 19:10:16 d2.data.datasets.coco]: Loaded 418 images in COCO format from /content/drive/My Drive/FoodSegmentation/data/val/annotations.json
[05/11 19:10:16 d2.data.common]: Serializing 418 elements to byte tensors and concatenating them all ...
[05/11 19:10:16 d2.data.common]: Serialized dataset takes 1.33 MiB
[05/11 19:10:16 d2.evaluation.evaluator]: Start inference on 418 images
[05/11 19:10:20 d2.evaluation.evaluator]: Inference done 11/418. 0.2834 s / img. ETA=0:02:18
[05/11 19:10:25 d2.evaluation.evaluator]: Inference done 25/418. 0.2833 s / img. ETA=0:02:18
[05/11 19:10:31 d2.evaluation.evaluator]: Inference done 39/418. 0.2852 s / img. ETA=0:02:19
[05/11 19:10:36 d2.evaluation.evaluator]: Inference done 51/418. 0.2885 s / img. ETA=0:02:21
[05/11 19:10:41 d2.evaluation.evaluator]: Inference done 64/418. 0.2890 s / img. ETA=0:02:18
[05/11 1

In [0]:
valResults

OrderedDict([('bbox',
              {'AP': 0.4349957763633505,
               'AP-almonds': 0.0,
               'AP-apple': 16.666666666666664,
               'AP-avocado': 0.0,
               'AP-banana': 5.247524752475248,
               'AP-beer': 0.0,
               'AP-biscuits': 0.0,
               'AP-boisson-au-glucose-50g': 0.0,
               'AP-bread-french-white-flour': 0.0,
               'AP-bread-sourdough': 0.0,
               'AP-bread-white': 0.0,
               'AP-bread-whole-wheat': 0.0,
               'AP-bread-wholemeal': 0.0,
               'AP-broccoli': 0.0,
               'AP-butter': 0.0,
               'AP-carrot': 0.0,
               'AP-cheese': 0.0,
               'AP-chicken': 0.0,
               'AP-chips-french-fries': 0.0,
               'AP-coffee-with-caffeine': 0.0,
               'AP-corn': nan,
               'AP-croissant': 0.0,
               'AP-cucumber': 0.0,
               'AP-dark-chocolate': 0.0,
               'AP-egg': 0.0,
          

In [0]:
model = torch.load("/content/drive/My Drive/FoodSegmentation/output/MaskRCNN_R_50_FPN_3x_1500epochs/model_final.pth",map_location=torch.device('cpu'))

In [0]:
model.keys()

dict_keys(['model', 'optimizer', 'scheduler', 'iteration'])

OrderedDict([('pixel_mean', tensor([[[103.5300]],
              
                      [[116.2800]],
              
                      [[123.6750]]])), ('pixel_std', tensor([[[1.]],
              
                      [[1.]],
              
                      [[1.]]])), ('backbone.fpn_lateral2.weight',
              tensor([[[[ 0.0002]],
              
                       [[-0.0111]],
              
                       [[ 0.0174]],
              
                       ...,
              
                       [[ 0.0069]],
              
                       [[-0.0159]],
              
                       [[ 0.0050]]],
              
              
                      [[[-0.0132]],
              
                       [[-0.0050]],
              
                       [[ 0.0011]],
              
                       ...,
              
                       [[ 0.0190]],
              
                       [[-0.0367]],
              
                       [[ 

In [0]:
file_path = "/content/drive/My Drive/FoodSegmentation/output/MaskRCNN_R_50_FPN_3x_1500epochs/last_checkpoint"
DetectionCheckpointer(model).load(file_path)

UnpicklingError: ignored

In [0]:

checkpointer = DetectionCheckpointer(model, save_dir="/content/drive/My Drive/FoodSegmentation/output/MaskRCNN_R_50_FPN_3x_1500epochs/")
checkpointer.save("model_999")

AttributeError: ignored

In [0]:
model.keys()

dict_keys(['model', 'optimizer', 'scheduler', 'iteration'])

In [0]:
model['optimizer'].keys()

dict_keys(['state', 'param_groups'])

In [0]:
model['scheduler'].keys()

dict_keys(['milestones', 'gamma', 'warmup_factor', 'warmup_iters', 'warmup_method', 'base_lrs', 'last_epoch', '_step_count', '_get_lr_called_within_step', '_last_lr'])

In [0]:
model['iteration'].keys()

AttributeError: ignored

In [0]:
model['optimizer']['state'].keys()

dict_keys([140275628066784, 140275628066856, 140275628067000, 140275628067144, 140275628067072, 140275628067360, 140275628067288, 140275628067576, 140275628067504, 140275628067792, 140275628067720, 140275628068008, 140275628067936, 140275628068224, 140275628068152, 140275628068440, 140276742934320, 140276742964784, 140276742964064, 140275628276688, 140275628276328, 140275628277264, 140275628275464, 140275628276184, 140275628274096, 140275628273808, 140275628274312, 140275637012736, 140275637012232, 140275637010864, 140275637014032, 140275637010648, 140275637012160, 140275637013096, 140275637013888, 140275637022656, 140275637022368, 140275637021288, 140275637021432, 140275637020280, 140275637020640, 140275637021072, 140275637137480, 140275637138488, 140275637138848, 140275637141080, 140275637139424, 140275637140576, 140275637140432, 140275637185344, 140275637184840, 140275637184408, 140275628389936, 140275628391664, 140275628392168, 140275628065128, 140275628065632, 140275628066136, 140

In [0]:
from detectron2.modeling import build_model



cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS = "/content/drive/My Drive/FoodSegmentation/output/MaskRCNN_R_50_FPN_3x_1500epochs/model_final.pth"
# cfg.MODEL.DEVICE = "cpu"
model = build_model(cfg)
DetectionCheckpointer(model).load(cfg.MODEL.WEIGHTS)

'roi_heads.box_predictor.cls_score.weight' has shape (62, 1024) in the checkpoint but (81, 1024) in the model! Skipped.
'roi_heads.box_predictor.cls_score.bias' has shape (62,) in the checkpoint but (81,) in the model! Skipped.
'roi_heads.box_predictor.bbox_pred.weight' has shape (244, 1024) in the checkpoint but (320, 1024) in the model! Skipped.
'roi_heads.box_predictor.bbox_pred.bias' has shape (244,) in the checkpoint but (320,) in the model! Skipped.
'roi_heads.mask_head.predictor.weight' has shape (61, 256, 1, 1) in the checkpoint but (80, 256, 1, 1) in the model! Skipped.
'roi_heads.mask_head.predictor.bias' has shape (61,) in the checkpoint but (80,) in the model! Skipped.


{'iteration': 1499,
 'optimizer': {'param_groups': [{'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    'nesterov': False,
    'params': [140275628066784],
    'weight_decay': 0.0001},
   {'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    'nesterov': False,
    'params': [140275628066856],
    'weight_decay': 0.0001},
   {'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    'nesterov': False,
    'params': [140275628067000],
    'weight_decay': 0.0001},
   {'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    'nesterov': False,
    'params': [140275628067144],
    'weight_decay': 0.0001},
   {'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    'nesterov': False,
    'params': [140275628067072],
    'weight_decay': 0.0001},
   {'dampening': 0,
    'initial_lr': 0.00025,
    'lr': 0.00025,
    'momentum': 0.9,
    

In [0]:
model.parameters()

<generator object Module.parameters at 0x7f31cdb28570>

In [0]:
type(model)

detectron2.modeling.meta_arch.rcnn.GeneralizedRCNN

In [0]:
model.keys()

AttributeError: ignored

In [0]:
DetectionCheckpointer(model).has_checkpoint()

False

In [0]:
model.state_dict()

OrderedDict([('pixel_mean', tensor([[[103.5300]],
              
                      [[116.2800]],
              
                      [[123.6750]]])), ('pixel_std', tensor([[[1.]],
              
                      [[1.]],
              
                      [[1.]]])), ('backbone.fpn_lateral2.weight',
              tensor([[[[ 0.0002]],
              
                       [[-0.0111]],
              
                       [[ 0.0174]],
              
                       ...,
              
                       [[ 0.0069]],
              
                       [[-0.0159]],
              
                       [[ 0.0050]]],
              
              
                      [[[-0.0132]],
              
                       [[-0.0050]],
              
                       [[ 0.0011]],
              
                       ...,
              
                       [[ 0.0190]],
              
                       [[-0.0367]],
              
                       [[ 

In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/data/train/images/")
os.listdir()[0]

'073476.jpg'

In [0]:
img_path = "/content/drive/My Drive/FoodSegmentation/data/train/images/073476.jpg"
im = cv2.imread(img_path)

In [0]:
im.shape

(796, 796, 3)

In [0]:
imtensor = torch.Tensor(im)

In [0]:
imtensor.shape

torch.Size([796, 796, 3])

In [0]:
imtensor = imtensor.view(imtensor.shape[2],imtensor.shape[0],imtensor.shape[1])

In [0]:
imtensor.shape

torch.Size([3, 796, 796])

In [0]:
outputs = model(imtensor)

IndexError: ignored

In [0]:
outputs = model(im)

IndexError: ignored

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/evaluations/coco_instances_results.json') as json_file:
    apr = json.load(json_file)
#automatic predicted results = apr    

In [0]:
apr

[{'bbox': [105.73371124267578,
   64.9184799194336,
   315.0834045410156,
   256.1061096191406],
  'category_id': 1040,
  'image_id': 6508,
  'score': 0.5154194831848145,
  'segmentation': {'counts': 'Th\\1c0`;d1TOc0@>I7N1O1N2O2N2M2O2M3N1O1N101L4L4K5O0O2O1N3N1N2O2M101O1O001O1O001O00001O0001O1O010O1O2N2N1O2N100O00001O1O001O001O001O1O2N2N2N1O1O2N1O1O1O1O1OO100000000O1[OPLPHP4n7SLQHm3m7VLRHj3k7ZLTHf3e7bLXH`3d7fLWH]3U6YLdJ?RO[3X6ZLbJj4]5YK^Jj4b5XKWJm4h5WKmIQ5R6T1O100O100O100000000000000000000O100000000000000O100000000000000000000000000001O000000000O10000000000000001O0000000O1000001O1O1O1O1O1N2O1O1O1O1O1O001O0O101O00001O0O101O4L3M4L4L5L7H9G8H3M3N0O1O0O101O000O1O1O2N1N2N2O2O1N101N101O0O2O0O2O00000001O01O0001O000001O1O1O0O2O1O001O0O2O001O0O2O0O2O0O2O1N3N1O2M2O2K4L5L3N3M2N2O2M3N2M3N1N2O1O0O2O001N101O0O101N100O2M2O2N100O2N1O1O2N1O1O2N1O2N101N2N1O2N1N4L3M5J6H9Ef];',
   'size': [426, 426]}},
 {'bbox': [63.930782318115234,
   69.42761993408203,
   304.336669921875,
   303.23101806640625],
  'categ

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/data/train/annotations.json') as json_file:
    train_anno = json.load(json_file)

In [0]:
train_anno.keys()

dict_keys(['categories', 'info', 'images', 'annotations'])

In [0]:
train_anno['categories']

[{'id': 2578,
  'name': 'water',
  'name_readable': 'Water',
  'supercategory': 'food'},
 {'id': 2939,
  'name': 'pizza-margherita-baked',
  'name_readable': 'Pizza, Margherita, baked',
  'supercategory': 'food'},
 {'id': 1085,
  'name': 'broccoli',
  'name_readable': 'Broccoli',
  'supercategory': 'food'},
 {'id': 1040,
  'name': 'salad-leaf-salad-green',
  'name_readable': 'Salad, leaf / salad, green',
  'supercategory': 'food'},
 {'id': 1070,
  'name': 'zucchini',
  'name_readable': 'Zucchini',
  'supercategory': 'food'},
 {'id': 2022, 'name': 'egg', 'name_readable': 'Egg', 'supercategory': 'food'},
 {'id': 2053,
  'name': 'butter',
  'name_readable': 'Butter',
  'supercategory': 'food'},
 {'id': 1566,
  'name': 'bread-white',
  'name_readable': 'Bread, white',
  'supercategory': 'food'},
 {'id': 1151,
  'name': 'apple',
  'name_readable': 'Apple',
  'supercategory': 'food'},
 {'id': 2131,
  'name': 'dark-chocolate',
  'name_readable': 'Dark chocolate',
  'supercategory': 'food'},
 

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/evaluations/coco_instances_results.json') as json_file:
    evaluations = json.load(json_file)

In [0]:
evaluations

[{'bbox': [105.73371124267578,
   64.9184799194336,
   315.0834045410156,
   256.1061096191406],
  'category_id': 1040,
  'image_id': 6508,
  'score': 0.5154194831848145,
  'segmentation': {'counts': 'Th\\1c0`;d1TOc0@>I7N1O1N2O2N2M2O2M3N1O1N101L4L4K5O0O2O1N3N1N2O2M101O1O001O1O001O00001O0001O1O010O1O2N2N1O2N100O00001O1O001O001O001O1O2N2N2N1O1O2N1O1O1O1O1OO100000000O1[OPLPHP4n7SLQHm3m7VLRHj3k7ZLTHf3e7bLXH`3d7fLWH]3U6YLdJ?RO[3X6ZLbJj4]5YK^Jj4b5XKWJm4h5WKmIQ5R6T1O100O100O100000000000000000000O100000000000000O100000000000000000000000000001O000000000O10000000000000001O0000000O1000001O1O1O1O1O1N2O1O1O1O1O1O001O0O101O00001O0O101O4L3M4L4L5L7H9G8H3M3N0O1O0O101O000O1O1O2N1N2N2O2O1N101N101O0O2O0O2O00000001O01O0001O000001O1O1O0O2O1O001O0O2O001O0O2O0O2O0O2O1N3N1O2M2O2K4L5L3N3M2N2O2M3N2M3N1N2O1O0O2O001N101O0O101N100O2M2O2N100O2N1O1O2N1O1O2N1O2N101N2N1O2N1N4L3M5J6H9Ef];',
   'size': [426, 426]}},
 {'bbox': [63.930782318115234,
   69.42761993408203,
   304.336669921875,
   303.23101806640625],
  'categ

###Proper Inference Code

In [0]:
import os
import json
from pycocotools.coco import COCO
from detectron2.engine import DefaultTrainer
from detectron2.config import get_cfg
from detectron2.structures import Boxes, BoxMode, pairwise_iou
import pycocotools.mask as mask_util

In [0]:
def instances_to_coco_json(instances, img_id):
    """
    Dump an "Instances" object to a COCO-format json that's used for evaluation.

    Args:
        instances (Instances):
        img_id (int): the image id

    Returns:
        list[dict]: list of json annotations in COCO format.
    """
    num_instance = len(instances)
    if num_instance == 0:
        return []

    boxes = instances.pred_boxes.tensor.numpy()
    boxes = BoxMode.convert(boxes, BoxMode.XYXY_ABS, BoxMode.XYWH_ABS)
    boxes = boxes.tolist()
    scores = instances.scores.tolist()
    classes = instances.pred_classes.tolist()

    has_mask = instances.has("pred_masks")
    if has_mask:
        # use RLE to encode the masks, because they are too large and takes memory
        # since this evaluator stores outputs of the entire dataset
        rles = [
            mask_util.encode(np.array(mask[:, :, None], order="F", dtype="uint8"))[0]
            for mask in instances.pred_masks
        ]
        for rle in rles:
            # "counts" is an array encoded by mask_util as a byte-stream. Python3's
            # json writer which always produces strings cannot serialize a bytestream
            # unless you decode it. Thankfully, utf-8 works out (which is also what
            # the pycocotools/_mask.pyx does).
            rle["counts"] = rle["counts"].decode("utf-8")

    has_keypoints = instances.has("pred_keypoints")
    if has_keypoints:
        keypoints = instances.pred_keypoints

    results = []
    for k in range(num_instance):
        result = {
            "image_id": img_id,
            "category_id": classes[k],
            "bbox": boxes[k],
            "score": scores[k],
        }
        if has_mask:
            result["segmentation"] = rles[k]
        if has_keypoints:
            # In COCO annotations,
            # keypoints coordinates are pixel indices.
            # However our predictions are floating point coordinates.
            # Therefore we subtract 0.5 to be consistent with the annotation format.
            # This is the inverse of data loading logic in `datasets/coco.py`.
            keypoints[k][:, :2] -= 0.5
            result["keypoints"] = keypoints[k].flatten().tolist()
        results.append(result)
    return results


In [0]:
#Random Variable Initialization
cpu_device = torch.device("cpu")
with open('/content/drive/My Drive/FoodSegmentation/reverse_id_mapping.json') as json_file:
    reverse_id_mapping = json.load(json_file)

In [0]:
cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS ="/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/model_final.pth"
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.2   # set the testing threshold for this model
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 61
predictor = DefaultPredictor(cfg)

In [0]:
results = []
os.chdir("/content/drive/My Drive/FoodSegmentation/data/train/images/")
countr = 0
for i in os.listdir():
  if(countr==5):
    break
  else:
    if('_' in i):
      i = i[2:]
      img_path = "/content/drive/My Drive/FoodSegmentation/data/train/images/" + i
    else:
      img_path ="/content/drive/My Drive/FoodSegmentation/data/train/images/" + i
  im = cv2.imread(img_path)
  # print(img_path)
  outputs = predictor(im)
  instances = outputs["instances"].to(cpu_device)
  # print(outputs)
  result = instances_to_coco_json(instances,i)
  if(len(result)==0):
    print("Nice ", result)
  else:
    for i in result:
      matchId = i['category_id']
      print(matchId)
      i['category_id'] = reverse_id_mapping[str(matchId)]
      results.append(i)  
  countr+=1  

Nice  []
Nice  []
51
53
Nice  []


In [0]:
results

[{'bbox': [68.58614349365234,
   83.56536865234375,
   254.75137329101562,
   272.29254150390625],
  'category_id': 2578,
  'image_id': '073508.jpg',
  'score': 0.8727155327796936,
  'segmentation': {'counts': 'dfS1<b=?F9H7H8G9I6J7J7I6K4I6L5K4L5L3M4L3M3M3M3O0O2N2O0O2N101N2N2N2M3N2N3L3N3L4M2N3L3N3L:G;E9F5L3M4K3N1N3N1N3M2O1N2O1N2O1O001N2O1O1O1O1O2N1N101N2O1N2O1O0O2O00010O0001O01O01O00000000O101O0000000000000000000000000001O000000000000001O00001O00001O001O000000001O0000001O001O0000001O00000000001O00000000001O000000000000001O000000001O000000001O0000001O00000000001O00001O001O00001O001O001O001O001O001O1O001O1O001O001O001O1O001O1N2O0jLjH[OW7c0mHhLIT2[7R1PI_L5W2m6V1fIgN[6W1iIfNY6V1mIfNU6V1oIhNS6S1RJkNP6Q1TJlNP6n0UJPOm5l0WJROk5k0WJTOk5h0YJUOk5g0XJWOl5c0XJ[Ol5`0XJ\\OQ68XJAV6LVJK_hQ2',
   'size': [455, 455]}},
 {'bbox': [100.84004974365234,
   102.5198974609375,
   199.336181640625,
   222.357666015625],
  'category_id': 2618,
  'image_id': '071607.jpg',
  'score': 0.8649392127990723,
  'segmenta

In [0]:
results

[[],
 [],
 [{'bbox': [68.58614349365234,
    83.56536865234375,
    254.75137329101562,
    272.29254150390625],
   'category_id': 51,
   'image_id': '073508.jpg',
   'score': 0.8727155327796936,
   'segmentation': {'counts': 'dfS1<b=?F9H7H8G9I6J7J7I6K4I6L5K4L5L3M4L3M3M3M3O0O2N2O0O2N101N2N2N2M3N2N3L3N3L4M2N3L3N3L:G;E9F5L3M4K3N1N3N1N3M2O1N2O1N2O1O001N2O1O1O1O1O2N1N101N2O1N2O1O0O2O00010O0001O01O01O00000000O101O0000000000000000000000000001O000000000000001O00001O00001O001O000000001O0000001O001O0000001O00000000001O00000000001O000000000000001O000000001O000000001O0000001O00000000001O00001O001O00001O001O001O001O001O001O1O001O1O001O001O001O1O001O1N2O0jLjH[OW7c0mHhLIT2[7R1PI_L5W2m6V1fIgN[6W1iIfNY6V1mIfNU6V1oIhNS6S1RJkNP6Q1TJlNP6n0UJPOm5l0WJROk5k0WJTOk5h0YJUOk5g0XJWOl5c0XJ[Ol5`0XJ\\OQ68XJAV6LVJK_hQ2',
    'size': [455, 455]}}],
 [{'bbox': [100.84004974365234,
    102.5198974609375,
    199.336181640625,
    222.357666015625],
   'category_id': 53,
   'image_id': '071607.jpg',
   'score': 0.864939

In [0]:
outputs

{'instances': Instances(num_instances=1, image_height=796, image_width=796, fields=[pred_boxes: Boxes(tensor([[189.2810, 137.3990, 693.7932, 677.5944]], device='cuda:0')), scores: tensor([0.2112], device='cuda:0'), pred_classes: tensor([2], device='cuda:0'), pred_masks: tensor([[[False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          ...,
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False],
          [False, False, False,  ..., False, False, False]]], device='cuda:0')])}

In [0]:
type(result)


list

In [0]:
result

[{'bbox': [189.28102111816406,
   137.3990020751953,
   504.51214599609375,
   540.1954345703125],
  'category_id': 2,
  'image_id': '073476.jpg',
  'score': 0.2111637443304062,
  'segmentation': {'counts': 'gTQ51U10^f05^YOL`f08]YOJ`f0:]YOG`f0>]YOCaf0a0[YOAcf0b0[YO_Ocf0e0YYO^Odf0e0YYO]Oef0f0XYO\\Ogf0f0VYO\\Oif0g0SYO\\Olf0Z1O1O1O1O2N1O1O1O2N1O1O1O2N1O1O100O1O2N1N2O1N2N2N2N2N2N2N2N20000O101N1O2O1N1O2O0O2N2N1O2O1N1O2N2N2N101N5K6K5K4K3N0O10001N100O100O2O000O100O1O2N101N1O2N1O2N2N1N3N1O2N1N3O1O0O2O001O000000001O0O1000001O000000001O00001O2M9H;E1O1O1O2N1O1N2O1O2N1O2N1O2N1O001O000000001O2N2N3L3N3M2N3M2N00001O00O100000000O1N2N2N2N2N2N2N2N2N2O1001O5K4L5K5K001O001O001O001O001O001O1O1O1O1O1O1O1O1O1O001O1O1O1O3M4L4L4L3MO1O100O1O1O1O1O1N2O1O1O1N2O1N2O10000002N3M2N3M2N2N3M2N1O1O1O1O1O1O1O2N1O00O1O1O100O1O100O1O1O100O1O1O1O1N2O12N3M1O2N1O1O1O1O1O1O1O1O1O1O1O1O1O1OO100O100O100O100O100O100O100O100O100O101O0O1000000O10001O00000O100000001O000000000O10001O00000000001N1000001N2J7D;J6N2N2N2N2N2N2O1N2N2N2N2O1

In [0]:
res = reverse_id_mapping['51']

In [0]:
type(res)

int

In [0]:
len(reverse_id_mapping)

61

###ABOVE CODE CHECKER

In [0]:
import os
import json
import torch, torchvision
import detectron2
import numpy as np
import cv2
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.structures import Boxes, BoxMode 
import pycocotools.mask as mask_util

In [0]:
test_images_path = AICROWD_TEST_IMAGES_PATH = "/content/drive/My Drive/FoodSegmentation/data/val/test_images/images/"
predictions_output_path= AICROWD_PREDICTIONS_OUTPUT_PATH = "/content/drive/My Drive/FoodSegmentation/"
model_path = "/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/model_final.pth"
cpu_device = torch.device("cpu")
reverse_id_mapping = {'0': 1010,'1': 1013,'10': 1068,'11': 1069,'12': 1070,'13': 1078,
 '14': 1085,'15': 1108,'16': 1116,'17': 1151,'18': 1154,'19': 1163,'2': 1022,'20': 1180,
 '21': 1210,'22': 1220,'23': 1307,'24': 1310,'25': 1311,'26': 1323,'27': 1352,'28': 1468,
 '29': 1505,'3': 1026,'30': 1520,'31': 1554,'32': 1556,'33': 1565,'34': 1566,'35': 1588,
 '36': 1788,'37': 1879,'38': 1893,'39': 1967,'4': 1032,'40': 2022,'41': 2053,'42': 2099,'43': 2103,
 '44': 2131,'45': 2388,'46': 2498,'47': 2504,'48': 2512,
 '49': 2521,'5': 1040,'50': 2530,'51': 2578,'52': 2580,'53': 2618,'54': 2620,'55': 2634,'56': 2711,
 '57': 2738,'58': 2750,'59': 2939,'6': 1056,'60': 3080,'7': 1058,'8': 1060,'9': 1061}

In [0]:
#GIVEN VARIABLES
# test_images_path = AICROWD_TEST_IMAGES_PATH = "/content/drive/My Drive/FoodSegmentation/data/val/test_images/images/"
# predictions_output_path= AICROWD_PREDICTIONS_OUTPUT_PATH = "/content/drive/My Drive/FoodSegmentation/"
# test_images_path, predictions_output_path
# reverse_id_mapping


In [0]:
def instances_to_coco_json(instances, img_id):
    num_instance = len(instances)
    if num_instance == 0:
        return []

    boxes = instances.pred_boxes.tensor.numpy()
    boxes = BoxMode.convert(boxes, BoxMode.XYXY_ABS, BoxMode.XYWH_ABS)
    boxes = boxes.tolist()
    scores = instances.scores.tolist()
    classes = instances.pred_classes.tolist()

    has_mask = instances.has("pred_masks")
    if has_mask:
        rles = [
            mask_util.encode(np.array(mask[:, :, None], order="F", dtype="uint8"))[0]
            for mask in instances.pred_masks
        ]
        for rle in rles:
            rle["counts"] = rle["counts"].decode("utf-8")

    has_keypoints = instances.has("pred_keypoints")
    if has_keypoints:
        keypoints = instances.pred_keypoints

    results = []
    for k in range(num_instance):
        result = {
            "image_id": img_id,
            "category_id": classes[k],
            "bbox": boxes[k],
            "score": scores[k],
        }
        if has_mask:
            result["segmentation"] = rles[k]
    
        results.append(result)
    return results







cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.WEIGHTS = model_path
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.2   # set the testing threshold for this model
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 61
cfg.MODEL.DEVICE = "cpu"
predictor = DefaultPredictor(cfg)

print("Done")

results = []
os.chdir(test_images_path)
for i in os.listdir():
  img_path =test_images_path + i
  im = cv2.imread(img_path)
  print(img_path)
  if(im is not None):
    outputs = predictor(im)
    instances = outputs["instances"].to(cpu_device)
    # print(outputs)
    fname = int(i.split('.')[0])
    result = instances_to_coco_json(instances,fname)
    if(len(result)!=0):
      for p in result:
        matchId = p['category_id']
        p['category_id'] = reverse_id_mapping[str(matchId)]
        results.append(p) 
  break  
  

Done
/content/drive/My Drive/FoodSegmentation/data/val/test_images/images/057781.jpg


TypeError: ignored

In [0]:
print(im)

None


In [0]:
len(results)

4

In [0]:
results

[{'bbox': [52.08071517944336,
   181.57908630371094,
   255.53289794921875,
   262.94940185546875],
  'category_id': 1013,
  'image_id': 57781,
  'score': 0.6863905787467957,
  'segmentation': {'counts': '`Yc1<b>4L3M2N3M3M2N2N3M2N2N3M2N2N2N3M3M3WC\\No;o1dC_NP<\\2J6K4K5J6J6H8J6K4M4M2O1N2O2M2N2M3N2N2N2N2N3L3L4L4K6L3N2N3M2O1N3M2N3M3M2N3N2N1O2N1O1O2O0O101O0O101O000000001O0O10001O0000000000001O000000001O0000001O00000000001O000000000000000000000000001O000000000000000000O1000000000000O1000000O10000O10000O2O000O100O10000O1000000O10000O1000000O2O0O10000O2N10001N101N101O0O2O001N101O001O001N101O001O0O2O1O001N101O0O2N3L4L9ETg`2',
   'size': [479, 480]}},
 {'bbox': [112.45894622802734,
   156.33412170410156,
   268.7756652832031,
   199.0680389404297],
  'category_id': 1154,
  'image_id': 57781,
  'score': 0.38022488355636597,
  'segmentation': {'counts': '_Sf1=^>8J3N3M2N2N2N2N3M2N2M3N2N1O1O2M2L4J6H9J5K5M3M3M3M3L4L4M3M3N2N2O1O1O1N2N2N2L5K4L4M3M3K5N2M3N2M3O1N2N200O1O1N2O1O1M3N2M3O10000O100O10000O100

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/evaluations/coco_instances_results.json') as json_file:
    predDict = json.load(json_file)

In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/")
with open("manual_val_results.json", "w") as write_file:
    json.dump(results, write_file)

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/manual_val_results.json') as json_file:
    manual_results = json.load(json_file)

In [0]:
len(manual_results)

3410

In [0]:
import random
import json
import numpy as np
import argparse
import base64
import glob
import os
from PIL import Image
from pycocotools.coco import COCO
from pycocotools.cocoeval import COCOeval
IMAGES_DIR = "/content/drive/My Drive/FoodSegmentation/data/val/images"
GROUND_TRUTH_ANNOTATION_PATH = "annotations.json"
ground_truth_annotations = COCO(GROUND_TRUTH_ANNOTATION_PATH)
submission_file = json.loads(open("/tmp/outputs.json").read())
results = ground_truth_annotations.loadRes(submission_file)
cocoEval = COCOeval(ground_truth_annotations, results, 'segm')
cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()
cocoEval = COCOeval(ground_truth_annotations, results, 'bbox')
cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()

In [0]:
import random
import json
import numpy as np
import argparse
import base64
import glob
import os
from PIL import Image
from pycocotools.coco import COCO
from pycocotools.cocoeval import COCOeval
IMAGES_DIR = "/content/drive/My Drive/FoodSegmentation/data/val/images"
GROUND_TRUTH_ANNOTATION_PATH = "/content/drive/My Drive/FoodSegmentation/data/val/annotations.json"
ground_truth_annotations = COCO(GROUND_TRUTH_ANNOTATION_PATH)
submission_file = json.loads(open("/content/drive/My Drive/FoodSegmentation/manual_val_results.json").read())
results = ground_truth_annotations.loadRes(submission_file)
cocoEval = COCOeval(ground_truth_annotations, results, 'segm')
cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()
cocoEval = COCOeval(ground_truth_annotations, results, 'bbox')
cocoEval.evaluate()
cocoEval.accumulate()
cocoEval.summarize()

loading annotations into memory...
Done (t=0.04s)
creating index...
index created!
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *segm*
DONE (t=0.86s).
Accumulating evaluation results...
DONE (t=0.36s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.109
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.183
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.116
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.032
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= large | maxDets=100 ] = 0.112
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets=  1 ] = 0.209
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets= 10 ] = 0.225
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets

In [0]:
with open('/content/drive/My Drive/FoodSegmentation/output/NewMASKRCNN_10000epochs/evaluations/coco_instances_results.json') as json_file:
    coco_val = json.load(json_file)

In [0]:
len(coco_val)

9283

In [0]:
coco_val

[{'bbox': [105.73371124267578,
   64.9184799194336,
   315.0834045410156,
   256.1061096191406],
  'category_id': 1040,
  'image_id': 6508,
  'score': 0.5154194831848145,
  'segmentation': {'counts': 'Th\\1c0`;d1TOc0@>I7N1O1N2O2N2M2O2M3N1O1N101L4L4K5O0O2O1N3N1N2O2M101O1O001O1O001O00001O0001O1O010O1O2N2N1O2N100O00001O1O001O001O001O1O2N2N2N1O1O2N1O1O1O1O1OO100000000O1[OPLPHP4n7SLQHm3m7VLRHj3k7ZLTHf3e7bLXH`3d7fLWH]3U6YLdJ?RO[3X6ZLbJj4]5YK^Jj4b5XKWJm4h5WKmIQ5R6T1O100O100O100000000000000000000O100000000000000O100000000000000000000000000001O000000000O10000000000000001O0000000O1000001O1O1O1O1O1N2O1O1O1O1O1O001O0O101O00001O0O101O4L3M4L4L5L7H9G8H3M3N0O1O0O101O000O1O1O2N1N2N2O2O1N101N101O0O2O0O2O00000001O01O0001O000001O1O1O0O2O1O001O0O2O001O0O2O0O2O0O2O1N3N1O2M2O2K4L5L3N3M2N2O2M3N2M3N1N2O1O0O2O001N101O0O101N100O2M2O2N100O2N1O1O2N1O1O2N1O2N101N2N1O2N1N4L3M5J6H9Ef];',
   'size': [426, 426]}},
 {'bbox': [63.930782318115234,
   69.42761993408203,
   304.336669921875,
   303.23101806640625],
  'categ

In [0]:
coco_val[0]

{'bbox': [105.73371124267578,
  64.9184799194336,
  315.0834045410156,
  256.1061096191406],
 'category_id': 1040,
 'image_id': 6508,
 'score': 0.5154194831848145,
 'segmentation': {'counts': 'Th\\1c0`;d1TOc0@>I7N1O1N2O2N2M2O2M3N1O1N101L4L4K5O0O2O1N3N1N2O2M101O1O001O1O001O00001O0001O1O010O1O2N2N1O2N100O00001O1O001O001O001O1O2N2N2N1O1O2N1O1O1O1O1OO100000000O1[OPLPHP4n7SLQHm3m7VLRHj3k7ZLTHf3e7bLXH`3d7fLWH]3U6YLdJ?RO[3X6ZLbJj4]5YK^Jj4b5XKWJm4h5WKmIQ5R6T1O100O100O100000000000000000000O100000000000000O100000000000000000000000000001O000000000O10000000000000001O0000000O1000001O1O1O1O1O1N2O1O1O1O1O1O001O0O101O00001O0O101O4L3M4L4L5L7H9G8H3M3N0O1O0O101O000O1O1O2N1N2N2O2O1N101N101O0O2O0O2O00000001O01O0001O000001O1O1O0O2O1O001O0O2O001O0O2O0O2O0O2O1N3N1O2M2O2K4L5L3N3M2N2O2M3N2M3N1N2O1O0O2O001N101O0O101N100O2M2O2N100O2N1O1O2N1O1O2N1O2N101N2N1O2N1N4L3M5J6H9Ef];',
  'size': [426, 426]}}

In [0]:
import random
import json
import numpy as np
import argparse
import base64
import glob
import os
import traceback
from PIL import Image
import aicrowd_helpers


import torch, torchvision
import detectron2
import cv2
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.structures import Boxes, BoxMode 
import pycocotools.mask as mask_util

"""
Expected ENVIRONMENT Variables

* AICROWD_TEST_IMAGES_PATH : abs path to  folder containing all the test images
* AICROWD_PREDICTIONS_OUTPUT_PATH : path where you are supposed to write the output predictions.json
"""

# Configuration Variables
padding = 50
SEGMENTATION_LENGTH = 10
MAX_NUMBER_OF_ANNOTATIONS = 10
# List of valid categories to choose from
VALID_CATEGORIES =  [2578, 2939, 1085, 1040, 1070, 2022, 2053, 1566, 1151, 2131, 2521, 1068, 1026, 2738, 1565, 2512, 1061, 1311, 1505, 1468, 1967, 1078, 1116, 1022, 2504, 1154, 1163, 2750, 1210, 2620, 1310, 1893, 1069, 1058, 1180, 2618, 1010, 1588, 1879, 3080, 2388, 1108, 1032, 2099, 2530, 1013, 1323, 2634, 1056, 1520, 1788, 1352, 2498, 2711, 2103, 1554, 1556, 1307, 1060, 1220, 2580]
model_path = "./model_final.pth"
cpu_device = torch.device("cpu")
reverse_id_mapping = {'0': 1010,'1': 1013,'10': 1068,'11': 1069,'12': 1070,'13': 1078,
 '14': 1085,'15': 1108,'16': 1116,'17': 1151,'18': 1154,'19': 1163,'2': 1022,'20': 1180,
 '21': 1210,'22': 1220,'23': 1307,'24': 1310,'25': 1311,'26': 1323,'27': 1352,'28': 1468,
 '29': 1505,'3': 1026,'30': 1520,'31': 1554,'32': 1556,'33': 1565,'34': 1566,'35': 1588,
 '36': 1788,'37': 1879,'38': 1893,'39': 1967,'4': 1032,'40': 2022,'41': 2053,'42': 2099,'43': 2103,
 '44': 2131,'45': 2388,'46': 2498,'47': 2504,'48': 2512,
 '49': 2521,'5': 1040,'50': 2530,'51': 2578,'52': 2580,'53': 2618,'54': 2620,'55': 2634,'56': 2711,
 '57': 2738,'58': 2750,'59': 2939,'6': 1056,'60': 3080,'7': 1058,'8': 1060,'9': 1061}

# Helper functions
def bounding_box_from_points(points):
    """
        This function only supports the `poly` format.
    """
    points = np.array(points).flatten()
    even_locations = np.arange(points.shape[0]/2) * 2
    odd_locations = even_locations + 1
    X = np.take(points, even_locations.tolist())
    Y = np.take(points, odd_locations.tolist())
    bbox = [X.min(), Y.min(), X.max()-X.min(), Y.max()-Y.min()]
    bbox = [int(b) for b in bbox]
    return bbox

def single_segmentation(image_width, image_height, number_of_points=10):
    points = []
    for k in range(number_of_points):
        # Choose a random x-coordinate
        random_x = int(random.randint(0, image_width))
        # Choose a random y-coordinate
        random_y = int(random.randint(0, image_height))
        #Flatly append them to the list of points
        points.append(random_x)
        points.append(random_y)
    return [points]

def single_annotation(image_id, number_of_points=10):
    width, height = get_image_width_height(image_id)
    _result = {}
    _result["image_id"] = image_id
    """
    Valid Categories are embedded in the annotations.json of the training set
    """
    _result["category_id"] = random.choice(VALID_CATEGORIES) 
    
    _result["score"] = np.random.rand() # a random score between 0 and 1

    _result["segmentation"] = single_segmentation(width, height, number_of_points=number_of_points)
    _result["bbox"] = bounding_box_from_points(_result["segmentation"])
    return _result


def get_image_id_from_image_path(image_path):
    """
    Returns the image_id from the image_path of a file in the test set
    image_path : /home/testsdir/098767.jpg 
    image_id : 98767
    """
    filename = os.path.basename(image_path)
    filename = filename.replace(".jpg", "")
    image_id = int(filename)
    return image_id

def gather_images(test_images_path):
    images = glob.glob(os.path.join(
        test_images_path, "*.jpg"
    ))
    return images

def gather_image_ids(test_images_path):
    images = gather_images(test_images_path)
    filenames = [os.path.basename(image_path).replace(".jpg","") for image_path in images]
    image_ids = [int(x) for x in filenames]
    return image_ids

def get_image_path(image_id):
    test_images_path = os.getenv("AICROWD_TEST_IMAGES_PATH", False)
    return "{}.jpg".format(os.path.join(test_images_path, str(image_id).zfill(6)))

def get_image_width_height(image_id):
    image_path = get_image_path(image_id)
    im = Image.open(image_path)
    width, height = im.size
    im.close()
    return width, height

def gather_input_output_path():
    test_images_path = os.getenv("AICROWD_TEST_IMAGES_PATH", False)
    assert test_images_path != False, "Please provide the path to the test images using the environment variable : AICROWD_TEST_IMAGES_PATH"

    predictions_output_path = os.getenv("AICROWD_PREDICTIONS_OUTPUT_PATH", False)
    assert predictions_output_path != False, "Please provide the output path (for writing the predictions.json) using the environment variable : AICROWD_PREDICTIONS_OUTPUT_PATH"

    return test_images_path, predictions_output_path

def instances_to_coco_json(instances, img_id):
    num_instance = len(instances)
    if num_instance == 0:
        return []

    boxes = instances.pred_boxes.tensor.numpy()
    boxes = BoxMode.convert(boxes, BoxMode.XYXY_ABS, BoxMode.XYWH_ABS)
    boxes = boxes.tolist()
    scores = instances.scores.tolist()
    classes = instances.pred_classes.tolist()

    has_mask = instances.has("pred_masks")
    if has_mask:
        rles = [
            mask_util.encode(np.array(mask[:, :, None], order="F", dtype="uint8"))[0]
            for mask in instances.pred_masks
        ]
        for rle in rles:
            rle["counts"] = rle["counts"].decode("utf-8")

    has_keypoints = instances.has("pred_keypoints")
    if has_keypoints:
        keypoints = instances.pred_keypoints

    results = []
    for k in range(num_instance):
        result = {
            "image_id": img_id,
            "category_id": classes[k],
            "bbox": boxes[k],
            "score": scores[k],
        }
        if has_mask:
            result["segmentation"] = rles[k]
    
        results.append(result)
    return results


def run():
    ########################################################################
    # Register Prediction Start
    ########################################################################
    aicrowd_helpers.execution_start()

    ########################################################################
    # Gather Input and Output paths from environment variables
    ########################################################################
    test_images_path, predictions_output_path = gather_input_output_path()

    ########################################################################
    # Generate Predictions
    ########################################################################
    cfg = get_cfg()
    cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
    cfg.MODEL.WEIGHTS = model_path
    cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.2   # set the testing threshold for this model
    cfg.MODEL.ROI_HEADS.NUM_CLASSES = 61
    predictor = DefaultPredictor(cfg)



    results = []
    os.chdir(test_images_path)
    for i in os.listdir():
      img_path =test_images_path + str(i)
      im = cv2.imread(img_path)
      outputs = predictor(im)
      instances = outputs["instances"].to(cpu_device)
      fname = int(i.split('.')[0])
      result = instances_to_coco_json(instances,fname)
      if(len(result)!=0):
        for i in result:
          matchId = i['category_id']
          i['category_id'] = reverse_id_mapping[str(matchId)]
          results.append(i)    
      aicrowd_helpers.execution_progress({
          "image_ids" : [fname]
      })


    # Write output
    fp = open(predictions_output_path, "w")
    fp.write(json.dumps(results))
    fp.close()
    ########################################################################
    # Register Prediction Complete
    ########################################################################
    aicrowd_helpers.execution_success({
        "predictions_output_path" : predictions_output_path
    })

if __name__ == "__main__":
    try:
        run()
    except Exception as e:
        error = traceback.format_exc()
        print(error)
        aicrowd_helpers.execution_error(error)


In [0]:
import os

In [0]:
os.chdir("/content/drive/My Drive/FoodSegmentation/data/val/images/")

In [0]:
countr = 0
for i in os.listdir():
  print(i)
  if(countr==20):
    break
  countr+=1  

._055218.jpg
052087.jpg
059497.jpg
031100.jpg
._055036.jpg
071948.jpg
._071780.jpg
._042673.jpg
011559.jpg
024298.jpg
052771.jpg
019453.jpg
._011559.jpg
._061736.jpg
073401.jpg
._052918.jpg
._039139.jpg
._016978.jpg
071780.jpg
._040742.jpg
017616.jpg


In [0]:
results = []
for i in os.listdir(test_images_path):
  img_path =test_images_path + "/" +str(i)
  im = cv2.imread(img_path)
  outputs = predictor(im)
  instances = outputs["instances"].to(cpu_device)
  fname = int(i.split('.')[0])
  result = instances_to_coco_json(instances,fname)
  if(len(result)!=0):
    for i in result:
      matchId = i['category_id']
      i['category_id'] = reverse_id_mapping[str(matchId)]
      results.append(i)    
  aicrowd_helpers.execution_progress({
      "image_ids" : [fname]
  })

In [0]:
yo = "huirguir"
str ="/hello/yoyo/" + "/" + yo

In [0]:
str

'/hello/yoyo//huirguir'

In [0]:
test_images_path = "/test/images"
x = "hellp"

In [0]:
if(test_images_path[-1]!='/'):
  img_path = test_images_path + '/' + str(x)
else:
  img_path = test_images_path + str(x)  

TypeError: ignored

In [0]:
img_path

'/test/images/hellp'

In [0]:
import os

In [0]:
for i in os.listdir("/content/drive/My Drive/FoodSegmentation/data/val/images/"):
  print(i)
  print(type(i))
  break

._055218.jpg
<class 'str'>
